In [1]:
from __future__ import (absolute_import, division, print_function)
import os
import json

import matplotlib as mpl
import matplotlib.pyplot as plt

from shapely.geometry import Point
import pandas as pd
import geopandas as gpd
from geopandas import GeoSeries, GeoDataFrame

data_path = "./data"

In [2]:
import geopandas as gpd
shapes = gpd.read_file( os.path.join(data_path, "MB_2016_NSW.shp") )
print(len(shapes))

103052


In [3]:
shapes.head()

MB_CODE16          MB_CAT16   SA1_MAIN16 SA1_7DIG16 SA2_MAIN16  \
0  10000009499  NOUSUALRESIDENCE  19999949999    1949999  199999499   
1  10000010000       Residential  10901117207    1117207  109011172   
2  10000021000        Commercial  10901117612    1117612  109011176   
3  10000022000        Commercial  10901117621    1117621  109011176   
4  10000023000        Commercial  10901117621    1117621  109011176   

  SA2_5DIG16              SA2_NAME16 SA3_CODE16              SA3_NAME16  \
0      19499  No usual address (NSW)      19999  No usual address (NSW)   
1      11172           Albury - East      10901                  Albury   
2      11176               Lavington      10901                  Albury   
3      11176               Lavington      10901                  Albury   
4      11176               Lavington      10901                  Albury   

  SA4_CODE16              SA4_NAME16 GCC_CODE16              GCC_NAME16  \
0        199  No usual address (NSW)      19499  No usual address (NSW)   
1        109                  Murray      1RNSW             Rest of NSW   
2        109                  Murray      1RNSW             Rest of NSW   
3        109                  Murray      1RNSW             Rest of NSW   
4        109                  Murray      1RNSW             Rest of NSW   

  STE_CODE16       STE_NAME16  AREASQKM16  \
0          1  New South Wales      0.0000   
1          1  New South Wales      0.0209   
2          1  New South Wales      0.0829   
3          1  New South Wales      0.0388   
4          1  New South Wales      0.0254   

                                            geometry  
0                                               None  
1  POLYGON ((146.92865 -36.08378, 146.92854 -36.0...  
2  POLYGON ((146.93262 -36.05108, 146.93224 -36.0...  
3  POLYGON ((146.93087 -36.05003, 146.93040 -36.0...  
4  POLYGON ((146.93253 -36.05240, 146.93100 -36.0...

In [4]:
shapes.head().geom_type

0       None
1    Polygon
2    Polygon
3    Polygon
4    Polygon
dtype: object

In [5]:
import psycopg2
import psycopg2.extras

def pgconnect_wk09(credential_filepath):
    try:
        with open(credential_filepath) as f:
            db_conn_dict = json.load(f)
        conn = psycopg2.connect(**db_conn_dict)
        print('connected')
    except Exception as e:
        print("unable to connect to the database")
        print(e)
        return None
    return conn


credfilepath = os.path.join("data2x01_db.json")
conn_wk09 = pgconnect_wk09(credfilepath)

connected


In [6]:
def pgquery_wk09( conn, sqlcmd, args=None, msg=False, returntype='tuple'):
    """ utility function to execute some SQL query statement
        it can take optional arguments (as a dictionary) to fill in for placeholders in the SQL
        will return the complete query result as return value - or in case of error: None
        error and transaction handling built-in (by using the 'with' clauses)"""
    retval = None
    with conn:
        cursortype = None if returntype != 'dict' else psycopg2.extras.RealDictCursor
        with conn.cursor(cursor_factory=cursortype) as cur:
            try:
                if args is None:
                    cur.execute(sqlcmd)
                else:
                    cur.execute(sqlcmd, args)
                if (cur.description != None ):
                    retval = cur.fetchall() # we use fetchall() as we expect only _small_ query results
                if msg != False:
                    print("success: " + msg)
            except psycopg2.DatabaseError as e:
                if e.pgcode != None:
                    if msg: print("db read error: "+msg)
                    print(e)
            except Exception as e:
                print(e)
    return retval

In [7]:
shapes_schema = '''CREATE TABLE shapes (
                     MB_CODE16 NUMERIC, 
                     MB_CAT16 VARCHAR(80), 
                     SA1_MAIN16 NUMERIC, 
                     SA1_7DIG16 NUMERIC, 
                     SA2_MAIN16 NUMERIC,
                     SA2_5DIG16 NUMERIC,
                     SA2_NAME16 VARCHAR(80),
                     SA3_CODE16 NUMERIC,
                     SA3_NAME16 VARCHAR(80),
                     SA4_CODE16 NUMERIC,
                     SA4_NAME16 VARCHAR(80),
                     GCC_CODE16 VARCHAR(80),
                     GCC_NAME16 VARCHAR(80),
                     STE_CODE16 NUMERIC,
                     STE_NAME16 VARCHAR(80),
                     AREASQKM16 NUMERIC,
                     geometry GEOMETRY(MULTIPOLYGON,4326))''' 

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS shapes", msg="cleared old table")
pgquery_wk09(conn_wk09, shapes_schema, msg="created shapes table")

success: cleared old table
success: created shapes table


In [8]:
insert_stmt = """INSERT INTO shapes VALUES ( %(MB_CODE16)s, %(MB_CAT16)s, %(SA1_MAIN16)s, %(SA1_7DIG16)s, 
                %(SA2_MAIN16)s, %(SA2_5DIG16)s,%(SA2_NAME16)s, %(SA3_CODE16)s, %(SA3_NAME16)s, %(SA4_CODE16)s, 
                %(SA4_NAME16)s, %(GCC_CODE16)s, %(GCC_NAME16)s, %(STE_CODE16)s, %(STE_NAME16)s, %(AREASQKM16)s,
                                            ST_Multi(ST_GeomFromText(%(geometry_wkt)s, 4326)) )"""


shapes['geometry_wkt'] = shapes['geometry'].apply(lambda x: x.wkt if x is not None else x)

for idx, shapes in shapes.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt, args=shapes, msg="inserted "+str(shapes['MB_CODE16']))
    

success: inserted 10000009499
success: inserted 10000010000
success: inserted 10000021000
success: inserted 10000022000
success: inserted 10000023000
success: inserted 10000024000
success: inserted 10000040000
success: inserted 10000050000
success: inserted 10000061000
success: inserted 10000062000
success: inserted 10000063000
success: inserted 10000070000
success: inserted 10000080000
success: inserted 10000090000
success: inserted 10000100000
success: inserted 10000110000
success: inserted 10000120000
success: inserted 10000130000
success: inserted 10000140000
success: inserted 10000151000
success: inserted 10000152000
success: inserted 10000161000
success: inserted 10000162000
success: inserted 10000170000
success: inserted 10000181000
success: inserted 10000183000
success: inserted 10000184000
success: inserted 10000185000
success: inserted 10000186000
success: inserted 10000190000
success: inserted 10000200000
success: inserted 10000210000
success: inserted 10000220000
success: i

In [10]:
index_command = "CREATE INDEX shapes_idx ON shapes USING GIST (geometry)"
result= pgquery_wk09(conn_wk09, index_command)
print(result)

relation "shapes_idx" already exists

None


In [35]:
StatisticalAreas_csv = pd.read_csv('StatisticalAreas.csv')

statistical_areas_schema = """CREATE TABLE IF NOT EXISTS statistical_areas (
                            area_id             NUMERIC PRIMARY KEY,
                            area_name           VARCHAR(100),
                            parent_area_id      NUMERIC)"""

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS statistical_areas", msg="cleared old table")
pgquery_wk09(conn_wk09, statistical_areas_schema, msg="created statistical_areas table")

insert_stmt = """INSERT INTO statistical_areas(area_id, area_name, parent_area_id)
                VALUES ( %(area_id)s, %(area_name)s, %(parent_area_id)s)"""

for idx, StatisticalAreas_csv in StatisticalAreas_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt, args=StatisticalAreas_csv)

success: cleared old table
success: created statistical_areas table


In [51]:
Neighbourhoods_csv = pd.read_csv('Neighbourhoods.csv')

neighbourhoods_schema = """CREATE TABLE IF NOT EXISTS neighbourhoods (
                            area_name                      VARCHAR(100) PRIMARY KEY,
                            area_id                        NUMERIC,
                            land_area                      NUMERIC,
                            population                     NUMERIC,
                            number_of_dwellings            NUMERIC,
                            number_of_businesses           NUMERIC,
                            median_annual_household_income NUMERIC,
                            avg_monthly_rent               NUMERIC)"""

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS neighbourhoods", msg="cleared old table")
pgquery_wk09(conn_wk09, neighbourhoods_schema, msg="created neighbourhoods table")

insert_stmt_2 = """INSERT INTO neighbourhoods(area_name, area_id, land_area, population, number_of_dwellings, 
                    number_of_businesses, median_annual_household_income, avg_monthly_rent)
                    VALUES ( %(area_name)s, %(area_id)s, %(land_area)s,%(population)s, %(number_of_dwellings)s, 
                    %(number_of_businesses)s, %(median_annual_household_income)s, %(avg_monthly_rent)s)"""

for idx, Neighbourhoods_csv in Neighbourhoods_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt_2, args=Neighbourhoods_csv)

success: cleared old table
success: created neighbourhoods table


In [52]:
PopulationStats2016_csv = pd.read_csv('PopulationStats2016.csv')

population_stats2016_schema = """CREATE TABLE IF NOT EXISTS population_stats2016 (
                            area_id       NUMERIC PRIMARY KEY,
                            area_name     VARCHAR(100),
                            "0-4"         NUMERIC,
                            "5-9"         NUMERIC,
                            "10-14"       NUMERIC,
                            "15-19"       NUMERIC,
                            "20-24"       NUMERIC,
                            "25-29"       NUMERIC,
                            "30-34"       NUMERIC,
                            "35-39"       NUMERIC,
                            "40-44"       NUMERIC,
                            "45-49"       NUMERIC,
                            "50-54"       NUMERIC,
                            "55-59"       NUMERIC,
                            "60-64"       NUMERIC,
                            "65-69"       NUMERIC,
                            "70-74"       NUMERIC,
                            "75-79"       NUMERIC,
                            "80-84"       NUMERIC,
                            "85_and_over" NUMERIC,
                            total_persons NUMERIC,
                            females       NUMERIC,
                            males         NUMERIC)"""


pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS population_stats2016", msg="cleared old table")
pgquery_wk09(conn_wk09, population_stats2016_schema, msg="created population_stats2016 table")

insert_stmt_3 = """INSERT INTO population_stats2016(area_id, area_name, "0-4", "5-9", "10-14", "15-19", 
                  "20-24", "25-29","30-34", "35-39", "40-44", "45-49", "50-54", "55-59", "60-64", "65-69", 
                  "70-74", "75-79", "80-84", "85_and_over", total_persons, females, males)
                   VALUES ( %(area_id)s, %(area_name)s, %(0-4)s, %(5-9)s, %(10-14)s, %(15-19)s,
                    %(20-24)s, %(25-29)s, %(30-34)s, %(35-39)s, %(40-44)s, %(45-49)s,%(50-54)s, 
                    %(55-59)s, %(60-64)s, %(65-69)s, %(70-74)s, %(75-79)s, %(80-84)s, %(85_and_over)s, 
                    %(total_persons)s, %(females)s, %(males)s)"""

for idx, PopulationStats2016_csv in PopulationStats2016_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt_3, args=PopulationStats2016_csv)

success: cleared old table
success: created population_stats2016 table


In [42]:
HealthServices_csv = pd.read_csv('HealthServices.csv')

health_services_schema = """CREATE TABLE IF NOT EXISTS health_services (
                            id         NUMERIC PRIMARY KEY,
                            name       VARCHAR(100),
                            category   VARCHAR(20),
                            address    VARCHAR(100),
                            suburb     VARCHAR(50),
                            state      CHAR(3),
                            postcode   NUMERIC,
                            longitude  NUMERIC,
                            latitude   NUMERIC)"""

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS health_services", msg="cleared old table")
pgquery_wk09(conn_wk09, health_services_schema, msg="created health_services table")

insert_stmt_4 = """INSERT INTO health_services(id, name, category, address, suburb, state, 
                    postcode, longitude, latitude)
                   VALUES ( %(id)s, %(name)s, %(category)s, %(address)s, %(suburb)s, %(state)s,
                   %(postcode)s, %(longitude)s, %(latitude)s)"""

for idx, HealthServices_csv in HealthServices_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt_4, args=HealthServices_csv)
    

success: cleared old table
success: created health_services table


In [40]:
NSW_Postcodes_csv = pd.read_csv('NSW_Postcodes.csv')

nsw_postcodes_schema = """CREATE TABLE IF NOT EXISTS nsw_postcodes (
                            id         INTEGER PRIMARY KEY,
                            postcode   INTEGER,
                            locality   VARCHAR(50),
                            longitude  NUMERIC,
                            latitude   NUMERIC)"""

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS nsw_postcodes", msg="cleared old table")
pgquery_wk09(conn_wk09, nsw_postcodes_schema, msg="created nsw_postcodes table")


insert_stmt_5 = """INSERT INTO nsw_postcodes(id, postcode, locality, longitude, latitude)
                   VALUES ( %(id)s, %(postcode)s, %(locality)s, %(longitude)s, %(latitude)s)"""

for idx, NSW_Postcodes_csv in NSW_Postcodes_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt_5, args=NSW_Postcodes_csv)

success: cleared old table
success: created nsw_postcodes table


In [41]:
covid19_nsw_testsites_simulated_capacity_csv = pd.read_csv('covid19_nsw_testsites_simulated_capacity.csv')

covid19_testsites_schema = """CREATE TABLE IF NOT EXISTS covid19_testsites (
                                site_id NUMERIC PRIMARY KEY, 
                                centre_name VARCHAR(100),
                                phone_number VARCHAR(70),
                                opening_hours VARCHAR(100),
                                longitude NUMERIC,
                                latitude NUMERIC,
                                test_capacity NUMERIC)"""

pgquery_wk09(conn_wk09, "DROP TABLE IF EXISTS covid19_testsites", msg="cleared old table")
pgquery_wk09(conn_wk09, covid19_testsites_schema, msg="created covid19_testsites table")

insert_stmt_6 = """INSERT INTO covid19_testsites(site_id, centre_name, phone_number, opening_hours, 
                   longitude, latitude, test_capacity)
                   VALUES ( %(site_id)s, %(Centre name)s, %(Phone number)s, %(Opening hours)s, 
                   %(longitude)s, %(latitude)s, %(test_capacity)s)"""

for idx, covid19_nsw_testsites_simulated_capacity_csv in covid19_nsw_testsites_simulated_capacity_csv.iterrows():
    pgquery_wk09(conn_wk09, insert_stmt_6, args=covid19_nsw_testsites_simulated_capacity_csv)
    

success: cleared old table
success: created covid19_testsites table


In [17]:
query = """CREATE INDEX postcodes_idx ON nsw_postcodes(postcode)"""
pgquery_wk09(conn_wk09, query)

In [53]:
create_table = """CREATE TABLE joined AS 
                 (SELECT * FROM neighbourhoods NATURAL JOIN population_stats2016)"""
pgquery_wk09(conn_wk09, create_table)


relation "joined" already exists



In [56]:
query = """SELECT * FROM joined WHERE area_name = 'Balmain'"""
pgquery_wk09(conn_wk09, query)

[(Decimal('120021387'),
  'Balmain',
  Decimal('258.2'),
  Decimal('16863.0'),
  Decimal('2494'),
  Decimal('2372.0'),
  Decimal('75494.0'),
  Decimal('2478.0'),
  Decimal('1118'),
  Decimal('1001'),
  Decimal('774'),
  Decimal('553'),
  Decimal('767'),
  Decimal('1127'),
  Decimal('1343'),
  Decimal('1443'),
  Decimal('1497'),
  Decimal('1322'),
  Decimal('1286'),
  Decimal('1078'),
  Decimal('1017'),
  Decimal('936'),
  Decimal('671'),
  Decimal('335'),
  Decimal('204'),
  Decimal('178'),
  Decimal('16650'),
  Decimal('8604'),
  Decimal('8046'))]

In [64]:
table = """CREATE TABLE health_data AS
            SELECT * 
            FROM joined, health_services
            WHERE joined.area_name = health_services.suburb"""
pgquery_wk09(conn_wk09, table)


In [70]:
QUERY = """CREATE TABLE health_data AS
            SELECT * FROM neighbourhoods, health_services
            WHERE health_services.suburb = neighbourhoods.area_name"""
pgquery_wk09(conn_wk09, QUERY)

In [69]:
hh = """DROP TABLE health_data"""
pgquery_wk09(conn_wk09, hh)

In [71]:
prnt = """SELECT * FROM health_data LIMIT 5"""
pgquery_wk09(conn_wk09, prnt)

[]